In [1]:
import numpy as np
import matplotlib.pyplot as plt
from matplotlib.animation import FFMpegWriter
from enum import Enum
from datetime import datetime
import os
import random
import copy

from PoolTable import *
from utils import *

## Ball-cloth interactions

### Physics analysis source: https://faculty.sites.iastate.edu/jia/files/inline-files/billiard-analysis.pdf

### Note: This analysis makes the assumption that $v$, $\omega$ have no z component i.e $v_z = 0$, $\omega_z = 0$.


$u$ = contact velocity

$v$ = center of mass's velocity

$R$ = ball's radius

$\hat{z}$ = unit z direction

$\omega$ = angular velocity

$\mu_s$ = coefficient of sliding friction

$\mu_r$ = coefficient of rolling friction

$\mu_w$ = coefficient of spinning friction 

### Sliding state (defined as $|u| \neq 0$ )

## $ \frac{\partial v}{\partial t} = -\mu_s g \cdot \hat{u} $

## $ \frac{\partial \omega_{xy}}{\partial t} = \frac{5}{2R} \mu_s g \cdot (\hat{z} \times \hat{u})$


### Rolling state (defined as $|u| = 0$ )

## $ \frac{\partial v}{\partial t} = -\frac{5}{7} \mu_r g \cdot \hat{v} $

No force that affects $\omega_{xy}$ directly, so 

## $ \omega_{xy} = \frac{1}{R}(\hat{z} \times v)$



### Stationary state
$ v = 0$, $\omega$ = 0


## Ball - Ball Interaction
### My model assumes perfectly elastic collisions, with only translational velocity transfer. The balls keep their angular velocity on impact

### Source:  https://en.wikipedia.org/wiki/Elastic_collision#Two-dimensional

## $ v_1' = v_1 - \frac{2m_2}{m_1 + m_2}\frac{<v_1 - v_2, x_1 - x_2>}{\lVert{x1 - x2}\rVert^2}(x_1 - x_2)$

## $ v_2' = v_2 - \frac{2m_1}{m_1 + m_2}\frac{<v_2 - v_1, x_2 - x_1>}{\lVert{x2 - x1}\rVert^2}(x_2 - x_1)$


## Ball - Table Interaction
### Same as above, but since the mass of table >>> ball, implemented as reflection of velocity

## Ball - Cue Interaction
### Source: WIll Leckze and MIchael Greenspan I, POOL PHYSICS SIMULATION BY EVENT PREDICTION 1: MOTION TRANSITIONS

#### Note: This analysis considers only the case where ball is hit by the cue in the downwards direction. My implementation adds a parameter $\phi$ which specifies the direction w.r.t the table so the ball can be hit in any direction.

$a$ = Horizontal distance from ball's center

$b$ = Vertical distance from ball's center

$\theta$ = Stick's angle from the horizontal plane

$\phi$ = Stick's shooting direction where 0 = left to right

### $ F = \frac{2 m V_{0}}{1 + \frac{m}{M} + \frac{5}{2R^2} (a^2 + b^2\cos^2\theta + c^2\sin^2\theta - 2bc\cos\theta \sin\theta)} $

### $ v = (0, \frac{-F}{m}\cos\theta, \frac{-F}{m}\sin\theta) $

### $ I = \frac{2}{5}mR^2$

### $ \omega = \frac{1}{I} (-cF\sin\theta + bF\cos\theta, aF\sin\theta, -aF\cos\theta)$

 $v$ and $\omega$ are rotated by $\phi$, then their z components are removed


In [2]:
# %matplotlib notebook
%matplotlib qt
plt.rcParams["figure.figsize"] = (20, 10)

In [3]:
def reset_table(writer=None, path_to_directory = None, targetFPS = 60, dt=1/240):
    table = PoolTable(writer, path_to_directory, targetFPS, dt)
    table.draw()
    cue = PoolBall(table, 30, table.y_lim/2, 'white')
    num=0
    for i in range(5):
        for j in range(5-i):
            x = table.x_lim - 35 - i*cue.radius*2
            mid = int((5-i)/2)+1
            if j < mid:
                y = table.y_lim/2+3 - ((mid-j)*cue.radius*2)
            else:
                y = table.y_lim/2+3 + (int(j-mid)*cue.radius*2)
            shift_up = 0 if i%2==0 else cue.radius
            num+=1
            PoolBall(table, x, y+shift_up,(random.uniform(0,1), random.uniform(0,1), random.uniform(0,1)), num=str(num))

    table.draw()
    return table, cue

In [4]:
metadata = dict(title='test', artist='Matplotlib')
writer = FFMpegWriter(fps=60, metadata=metadata, bitrate=200000)

In [8]:
table, cue = reset_table(writer=writer, path_to_directory="test")

print(cue.y)
cue.y[1] = table.balls[-1].y[1]
table.draw()

10.0 100
[30.     63.5     2.8575  0.      0.      0.      0.      0.      0.    ]


In [190]:
t1 = datetime.now()

# Uncomment these lines to restore last checkpoint
# table.balls = ckpt_balls
# cue=table.get_cue()
# assert cue != None
# table.draw()

# Make checkpoint
ckpt_balls = copy.deepcopy(table.balls)

#Simulate
table.cue_strike(cue, cue_velocity=150, theta=0, a=0, b=0, phi=0)

t2 = datetime.now()
print(f"done in {t2-t1}")


Starting simulation
Done
done in 0:00:44.461274
